In [1]:
import pandas as pd
import numpy as np
import torch
import torch.nn as nn
from torch.utils.data import TensorDataset, DataLoader
from torch import Tensor
import torch.nn.functional as F
from torch.optim.lr_scheduler import MultiStepLR
from torch.utils.tensorboard import SummaryWriter

In [2]:
writer = SummaryWriter()

In [3]:
train_set = pd.read_csv("data/final_format/train_set.csv",header=None).to_numpy()
train_label = pd.read_csv("data/final_format/train_label.csv",header=None).to_numpy()
test_set = pd.read_csv("data/final_format/test_set.csv",header=None).to_numpy()
test_label = pd.read_csv("data/final_format/test_label.csv",header=None).to_numpy()

In [4]:
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14393, 4096) (14393, 1) (3599, 4096) (3599, 1)


In [5]:
#delet first row data
train_set = train_set[1:]
train_label = train_label[1:]
test_set = test_set[1:]
test_label = test_label[1:]
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 4096) (14392, 1) (3598, 4096) (3598, 1)


In [6]:
train_set = train_set.reshape((-1,1,64,64))
test_set = test_set.reshape((-1,1,64,64))
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 1, 64, 64) (14392, 1) (3598, 1, 64, 64) (3598, 1)


In [7]:
train_label = train_label.reshape(-1)
test_label = test_label.reshape(-1)

print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 1, 64, 64) (14392,) (3598, 1, 64, 64) (3598,)


In [8]:
# Hyper parameters
num_epochs = 300
num_classes = 4
batch_size = 64
learning_rate = 1e-3

In [9]:
train_set_tensor = Tensor(train_set) 
train_label_tensor = Tensor(train_label).type(torch.LongTensor)

train_dataset = TensorDataset(train_set_tensor,train_label_tensor) 
train_loader = DataLoader(train_dataset, batch_size=batch_size) 

test_set_tensor = Tensor(test_set) 
test_label_tensor = Tensor(test_label).type(torch.LongTensor)

test_dataset = TensorDataset(test_set_tensor,test_label_tensor) 
test_loader = DataLoader(test_dataset, batch_size=batch_size) 

In [10]:
# Device configuration
device = torch.device('cuda:0' if torch.cuda.is_available() else 'cpu')
device

device(type='cuda', index=0)

In [31]:
# Convolutional neural network (two convolutional layers)
class ResNet(nn.Module):
    def __init__(self, num_classes=4):
        super(ResNet, self).__init__()
        self.c1 = nn.Conv2d(1, 32, kernel_size=1, padding='same')
        self.c2 = nn.Conv2d(32, 32, kernel_size=3,padding='same')
        self.c3 = nn.Conv2d(33, 64, kernel_size=3,padding='same')
        self.c4 = nn.Conv2d(64, 64, kernel_size=3, padding='same')
        self.c5 = nn.Conv2d(97, 128, kernel_size=3,padding='same')
        self.c6 = nn.Conv2d(128, 128, kernel_size=3, padding='same')
        
        self.d1 = nn.Dropout(p=0.25)
        self.d2 = nn.Dropout(p=0.25)
        self.d3 = nn.Dropout(p=0.25)
        self.d4 = nn.Dropout(p=0.25)
        self.d5 = nn.Dropout(p=0.25)
        self.d6 = nn.Dropout(p=0.25)
        self.d7 = nn.Dropout(p=0.25)
        
        self.bn1 =  nn.BatchNorm2d(1)
        self.bn2 =  nn.BatchNorm2d(32)
        self.bn3 =  nn.BatchNorm2d(33)
        self.bn4 =  nn.BatchNorm2d(64)
        self.bn5 =  nn.BatchNorm2d(97)
        self.bn6 =  nn.BatchNorm2d(128)
        self.bn7 =  nn.BatchNorm1d(512)
        
        self.fc1 = nn.Linear(225*8*8, 512)
        self.fc2 = nn.Linear(512, num_classes)
        
        
    def forward(self, x):
        C1 = self.c1(self.bn1(x))
        C1 = F.leaky_relu(C1,0.2)
        C1 = self.d1(C1)
        C2 = self.c2(self.bn2(C1))
        sum1 = torch.cat((x, C2), dim=1)
        sum1 = F.leaky_relu(sum1,0.2)
        sum1 = self.d2(sum1)
        M1 = F.max_pool2d(sum1, kernel_size=2, stride=2)
         
        C3 = self.c3(self.bn3(M1))
        C3 = F.leaky_relu(C3,0.2)
        C3 = self.d3(C3)
        C4 = self.c4(self.bn4(C3))
        sum2 = torch.cat((M1, C4), dim=1)
        sum2 = F.leaky_relu(sum2,0.2)
        sum2 = self.d4(sum2)
        M2 = F.max_pool2d(sum2, kernel_size=2, stride=2)
          
        C5 = self.c5(self.bn5(M2))
        C5 = F.leaky_relu(C5,0.2)
        C5 = self.d5(C5)
        C6 = self.c6(self.bn6(C5))
        sum3 = torch.cat((M2, C6), dim=1)
        sum3 = F.leaky_relu(sum3,0.2)
        sum3 = self.d6(sum3)
        M3 = F.max_pool2d(sum3, kernel_size=2, stride=2)
        
        F1 = M3.reshape(M3.size(0), -1)
        Fc1 = self.fc1(F1)
        Fc1 = self.bn7(Fc1)
        Fc1 = F.leaky_relu(Fc1,0.2)
        Fc1 = self.d7(Fc1)
        Fc2 = self.fc2(Fc1)
       
        return Fc2
    


In [32]:
model = ResNet(num_classes).to(device)

In [33]:
# Loss and optimizer
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate, weight_decay=1e-3) 
#optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate) 
milestones = [50,100,150,200,250]
milestones = [a * len(train_loader) for a in milestones]
scheduler = MultiStepLR(optimizer, milestones=milestones, gamma=0.5)

In [34]:
# Train the model
total_step = len(train_loader)
for epoch in range(num_epochs):
    correct=0
    total=0
    running_loss = 0
    for i, (X, Y) in enumerate(train_loader):
        X = X.to(device)
        Y = Y.to(device)
        
        
        # Forward pass
        outputs = model(X)
        loss = criterion(outputs, Y)
        
        # Backward and optimize
        optimizer.zero_grad()
        loss.backward()
        #scheduler.step() 
        #print(scheduler.get_last_lr()[0])
      
        optimizer.step()
        scheduler.step() 
        #print(optimizer.param_groups[0]["lr"])
        
        _, predicted = outputs.max(1)
        total += Y.size(0)
        correct += predicted.eq(Y).sum().item()
        running_loss += loss.item()
        accu=100.*correct/total
        train_loss = running_loss/(i+1)
        print ('Epoch [{}/{}], Step [{}/{}], Training Accuracy: {:.4f}%, Training Loss: {:.4f}%'.format(epoch+1, num_epochs, i+1, total_step, accu, train_loss))
    
   
        #writer.add_scalar(f'train/accuracy', accu, epoch)
        #writer.add_scalar(f'train/loss', train_loss, epoch)
        writer.add_scalars(f'train/accuracy_loss', {
            'accuracy': accu,
            'loss': train_loss,
        }, epoch)
        
        

Epoch [1/300], Step [1/225], Training Accuracy: 28.1250%, Training Loss: 1.5506%
Epoch [1/300], Step [2/225], Training Accuracy: 28.9062%, Training Loss: 56.4850%
Epoch [1/300], Step [3/225], Training Accuracy: 27.0833%, Training Loss: 61.9703%
Epoch [1/300], Step [4/225], Training Accuracy: 27.3438%, Training Loss: 51.3761%
Epoch [1/300], Step [5/225], Training Accuracy: 25.9375%, Training Loss: 47.2340%
Epoch [1/300], Step [6/225], Training Accuracy: 26.0417%, Training Loss: 43.9296%
Epoch [1/300], Step [7/225], Training Accuracy: 25.0000%, Training Loss: 43.5640%
Epoch [1/300], Step [8/225], Training Accuracy: 25.1953%, Training Loss: 40.9122%
Epoch [1/300], Step [9/225], Training Accuracy: 25.0000%, Training Loss: 39.9092%
Epoch [1/300], Step [10/225], Training Accuracy: 25.9375%, Training Loss: 38.0317%
Epoch [1/300], Step [11/225], Training Accuracy: 26.1364%, Training Loss: 37.0273%
Epoch [1/300], Step [12/225], Training Accuracy: 26.0417%, Training Loss: 35.8446%
Epoch [1/300],

Epoch [1/300], Step [108/225], Training Accuracy: 27.3582%, Training Loss: 6.8720%
Epoch [1/300], Step [109/225], Training Accuracy: 27.4943%, Training Loss: 6.8235%
Epoch [1/300], Step [110/225], Training Accuracy: 27.4716%, Training Loss: 6.7821%
Epoch [1/300], Step [111/225], Training Accuracy: 27.5056%, Training Loss: 6.7357%
Epoch [1/300], Step [112/225], Training Accuracy: 27.5251%, Training Loss: 6.6899%
Epoch [1/300], Step [113/225], Training Accuracy: 27.5581%, Training Loss: 6.6462%
Epoch [1/300], Step [114/225], Training Accuracy: 27.5630%, Training Loss: 6.6014%
Epoch [1/300], Step [115/225], Training Accuracy: 27.5408%, Training Loss: 6.5603%
Epoch [1/300], Step [116/225], Training Accuracy: 27.6401%, Training Loss: 6.5169%
Epoch [1/300], Step [117/225], Training Accuracy: 27.5507%, Training Loss: 6.4766%
Epoch [1/300], Step [118/225], Training Accuracy: 27.5291%, Training Loss: 6.4370%
Epoch [1/300], Step [119/225], Training Accuracy: 27.5867%, Training Loss: 6.3982%
Epoc

Epoch [1/300], Step [208/225], Training Accuracy: 28.1100%, Training Loss: 4.4127%
Epoch [1/300], Step [209/225], Training Accuracy: 28.1175%, Training Loss: 4.3985%
Epoch [1/300], Step [210/225], Training Accuracy: 28.0804%, Training Loss: 4.3853%
Epoch [1/300], Step [211/225], Training Accuracy: 28.0880%, Training Loss: 4.3711%
Epoch [1/300], Step [212/225], Training Accuracy: 28.0808%, Training Loss: 4.3570%
Epoch [1/300], Step [213/225], Training Accuracy: 28.1030%, Training Loss: 4.3435%
Epoch [1/300], Step [214/225], Training Accuracy: 28.0958%, Training Loss: 4.3301%
Epoch [1/300], Step [215/225], Training Accuracy: 28.0160%, Training Loss: 4.3178%
Epoch [1/300], Step [216/225], Training Accuracy: 28.0744%, Training Loss: 4.3042%
Epoch [1/300], Step [217/225], Training Accuracy: 28.1250%, Training Loss: 4.2902%
Epoch [1/300], Step [218/225], Training Accuracy: 28.1537%, Training Loss: 4.2781%
Epoch [1/300], Step [219/225], Training Accuracy: 28.1393%, Training Loss: 4.2661%
Epoc

Epoch [2/300], Step [83/225], Training Accuracy: 30.4405%, Training Loss: 1.4179%
Epoch [2/300], Step [84/225], Training Accuracy: 30.4688%, Training Loss: 1.4166%
Epoch [2/300], Step [85/225], Training Accuracy: 30.4963%, Training Loss: 1.4166%
Epoch [2/300], Step [86/225], Training Accuracy: 30.5414%, Training Loss: 1.4155%
Epoch [2/300], Step [87/225], Training Accuracy: 30.5496%, Training Loss: 1.4170%
Epoch [2/300], Step [88/225], Training Accuracy: 30.4510%, Training Loss: 1.4179%
Epoch [2/300], Step [89/225], Training Accuracy: 30.4249%, Training Loss: 1.4185%
Epoch [2/300], Step [90/225], Training Accuracy: 30.4167%, Training Loss: 1.4185%
Epoch [2/300], Step [91/225], Training Accuracy: 30.3400%, Training Loss: 1.4253%
Epoch [2/300], Step [92/225], Training Accuracy: 30.2310%, Training Loss: 1.4305%
Epoch [2/300], Step [93/225], Training Accuracy: 30.2923%, Training Loss: 1.4323%
Epoch [2/300], Step [94/225], Training Accuracy: 30.3191%, Training Loss: 1.4309%
Epoch [2/300], S

Epoch [2/300], Step [189/225], Training Accuracy: 31.5972%, Training Loss: 1.4062%
Epoch [2/300], Step [190/225], Training Accuracy: 31.5461%, Training Loss: 1.4068%
Epoch [2/300], Step [191/225], Training Accuracy: 31.4791%, Training Loss: 1.4076%
Epoch [2/300], Step [192/225], Training Accuracy: 31.4860%, Training Loss: 1.4072%
Epoch [2/300], Step [193/225], Training Accuracy: 31.5253%, Training Loss: 1.4066%
Epoch [2/300], Step [194/225], Training Accuracy: 31.5802%, Training Loss: 1.4060%
Epoch [2/300], Step [195/225], Training Accuracy: 31.5785%, Training Loss: 1.4058%
Epoch [2/300], Step [196/225], Training Accuracy: 31.5370%, Training Loss: 1.4061%
Epoch [2/300], Step [197/225], Training Accuracy: 31.4959%, Training Loss: 1.4067%
Epoch [2/300], Step [198/225], Training Accuracy: 31.5025%, Training Loss: 1.4058%
Epoch [2/300], Step [199/225], Training Accuracy: 31.4777%, Training Loss: 1.4057%
Epoch [2/300], Step [200/225], Training Accuracy: 31.4844%, Training Loss: 1.4054%
Epoc

...

Epoch [299/300], Step [5/225], Training Accuracy: 99.0625%, Training Loss: 0.0204%
Epoch [299/300], Step [6/225], Training Accuracy: 99.2188%, Training Loss: 0.0177%
Epoch [299/300], Step [7/225], Training Accuracy: 99.1071%, Training Loss: 0.0195%
Epoch [299/300], Step [8/225], Training Accuracy: 99.2188%, Training Loss: 0.0184%
Epoch [299/300], Step [9/225], Training Accuracy: 99.3056%, Training Loss: 0.0169%
Epoch [299/300], Step [10/225], Training Accuracy: 99.2188%, Training Loss: 0.0193%
Epoch [299/300], Step [11/225], Training Accuracy: 99.2898%, Training Loss: 0.0181%
Epoch [299/300], Step [12/225], Training Accuracy: 99.3490%, Training Loss: 0.0189%
Epoch [299/300], Step [13/225], Training Accuracy: 99.3990%, Training Loss: 0.0182%
Epoch [299/300], Step [14/225], Training Accuracy: 99.4420%, Training Loss: 0.0173%
Epoch [299/300], Step [15/225], Training Accuracy: 99.4792%, Training Loss: 0.0173%
Epoch [299/300], Step [16/225], Training Accuracy: 99.5117%, Training Loss: 0.017

Epoch [299/300], Step [108/225], Training Accuracy: 99.6817%, Training Loss: 0.0148%
Epoch [299/300], Step [109/225], Training Accuracy: 99.6846%, Training Loss: 0.0148%
Epoch [299/300], Step [110/225], Training Accuracy: 99.6875%, Training Loss: 0.0147%
Epoch [299/300], Step [111/225], Training Accuracy: 99.6903%, Training Loss: 0.0146%
Epoch [299/300], Step [112/225], Training Accuracy: 99.6931%, Training Loss: 0.0147%
Epoch [299/300], Step [113/225], Training Accuracy: 99.6958%, Training Loss: 0.0147%
Epoch [299/300], Step [114/225], Training Accuracy: 99.6985%, Training Loss: 0.0147%
Epoch [299/300], Step [115/225], Training Accuracy: 99.7011%, Training Loss: 0.0146%
Epoch [299/300], Step [116/225], Training Accuracy: 99.7037%, Training Loss: 0.0146%
Epoch [299/300], Step [117/225], Training Accuracy: 99.7062%, Training Loss: 0.0145%
Epoch [299/300], Step [118/225], Training Accuracy: 99.7087%, Training Loss: 0.0144%
Epoch [299/300], Step [119/225], Training Accuracy: 99.7111%, Tra

Epoch [299/300], Step [211/225], Training Accuracy: 99.6445%, Training Loss: 0.0148%
Epoch [299/300], Step [212/225], Training Accuracy: 99.6389%, Training Loss: 0.0148%
Epoch [299/300], Step [213/225], Training Accuracy: 99.6406%, Training Loss: 0.0149%
Epoch [299/300], Step [214/225], Training Accuracy: 99.6422%, Training Loss: 0.0148%
Epoch [299/300], Step [215/225], Training Accuracy: 99.6439%, Training Loss: 0.0148%
Epoch [299/300], Step [216/225], Training Accuracy: 99.6455%, Training Loss: 0.0149%
Epoch [299/300], Step [217/225], Training Accuracy: 99.6400%, Training Loss: 0.0149%
Epoch [299/300], Step [218/225], Training Accuracy: 99.6416%, Training Loss: 0.0150%
Epoch [299/300], Step [219/225], Training Accuracy: 99.6361%, Training Loss: 0.0150%
Epoch [299/300], Step [220/225], Training Accuracy: 99.6378%, Training Loss: 0.0150%
Epoch [299/300], Step [221/225], Training Accuracy: 99.6394%, Training Loss: 0.0150%
Epoch [299/300], Step [222/225], Training Accuracy: 99.6410%, Tra

Epoch [300/300], Step [89/225], Training Accuracy: 99.7893%, Training Loss: 0.0135%
Epoch [300/300], Step [90/225], Training Accuracy: 99.7917%, Training Loss: 0.0136%
Epoch [300/300], Step [91/225], Training Accuracy: 99.7940%, Training Loss: 0.0136%
Epoch [300/300], Step [92/225], Training Accuracy: 99.7962%, Training Loss: 0.0135%
Epoch [300/300], Step [93/225], Training Accuracy: 99.7984%, Training Loss: 0.0134%
Epoch [300/300], Step [94/225], Training Accuracy: 99.8005%, Training Loss: 0.0133%
Epoch [300/300], Step [95/225], Training Accuracy: 99.8026%, Training Loss: 0.0134%
Epoch [300/300], Step [96/225], Training Accuracy: 99.8047%, Training Loss: 0.0133%
Epoch [300/300], Step [97/225], Training Accuracy: 99.8067%, Training Loss: 0.0134%
Epoch [300/300], Step [98/225], Training Accuracy: 99.8087%, Training Loss: 0.0133%
Epoch [300/300], Step [99/225], Training Accuracy: 99.8106%, Training Loss: 0.0132%
Epoch [300/300], Step [100/225], Training Accuracy: 99.7969%, Training Loss:

Epoch [300/300], Step [191/225], Training Accuracy: 99.7546%, Training Loss: 0.0137%
Epoch [300/300], Step [192/225], Training Accuracy: 99.7559%, Training Loss: 0.0137%
Epoch [300/300], Step [193/225], Training Accuracy: 99.7490%, Training Loss: 0.0138%
Epoch [300/300], Step [194/225], Training Accuracy: 99.7342%, Training Loss: 0.0141%
Epoch [300/300], Step [195/225], Training Accuracy: 99.7356%, Training Loss: 0.0141%
Epoch [300/300], Step [196/225], Training Accuracy: 99.7290%, Training Loss: 0.0142%
Epoch [300/300], Step [197/225], Training Accuracy: 99.7303%, Training Loss: 0.0141%
Epoch [300/300], Step [198/225], Training Accuracy: 99.7238%, Training Loss: 0.0142%
Epoch [300/300], Step [199/225], Training Accuracy: 99.7252%, Training Loss: 0.0142%
Epoch [300/300], Step [200/225], Training Accuracy: 99.7266%, Training Loss: 0.0141%
Epoch [300/300], Step [201/225], Training Accuracy: 99.7279%, Training Loss: 0.0142%
Epoch [300/300], Step [202/225], Training Accuracy: 99.7293%, Tra

In [35]:
# Test the model
model.eval()  # eval mode (batchnorm uses moving mean/variance instead of mini-batch mean/variance)
with torch.no_grad():
    correct = 0
    total = 0
    for X, Y in test_loader:
        X = X.to(device)
        Y = Y.to(device)
        outputs = model(X)
        _, predicted = torch.max(outputs.data, 1)
        total += Y.size(0)
        correct += (predicted == Y).sum().item()

    print('Test Accuracy : {} %'.format(100 * correct / total))

# Save the model checkpoint
#torch.save(model.state_dict(), 'model.ckpt')

Test Accuracy : 72.95719844357977 %
